In [1]:
! pip install contractions
! pip install -U accelerate
! pip install -U transformers


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 289.9/289.9 kB 15.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.7/110.7 kB 28.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.6/302.6 kB 4.5 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 25.9 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 401.3/401.3 kB 44.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.8/43.8 kB 1.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.9/40.9 kB 7.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.1/9.1 MB 51.7 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 775.1/775.1 kB 85.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.6/3.6 MB 119.2 MB/s eta 0:00:00


# Yeni Bölüm

In [34]:
!pip install pandas
!pip install nltk
!pip install scikit-learn
!pip install pyarrow
!pip install fastparquet
!pip install openpyxl

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 250.0/250.0 kB 9.5 MB/s eta 0:00:00


In [35]:
#from google.colab import drive
#drive.mount('/content/drive',force_remount=True)

In [36]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import os
import pandas as pd
import numpy as np
import re
import contractions
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer

from torch.utils.data import Dataset, DataLoader
from transformers import AdamW
from collections import defaultdict
import time
from torch.utils.data import DataLoader, TensorDataset
from sklearn.model_selection import train_test_split

In [39]:

## Load the BERT model
from transformers import BertTokenizer, BertModel
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = BertModel.from_pretrained("bert-base-uncased")

print(model)

BertModel(
  (embeddings): BertEmbeddings(
    (word_embeddings): Embedding(30522, 768, padding_idx=0)
    (position_embeddings): Embedding(512, 768)
    (token_type_embeddings): Embedding(2, 768)
    (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (encoder): BertEncoder(
    (layer): ModuleList(
      (0-11): 12 x BertLayer(
        (attention): BertAttention(
          (self): BertSdpaSelfAttention(
            (query): Linear(in_features=768, out_features=768, bias=True)
            (key): Linear(in_features=768, out_features=768, bias=True)
            (value): Linear(in_features=768, out_features=768, bias=True)
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (output): BertSelfOutput(
            (dense): Linear(in_features=768, out_features=768, bias=True)
            (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
            (dropout): Dropout(p=0.1, inplace=False

In [41]:
# Load the model weights using hugingface model hub
from transformers import BertTokenizer, BertModel
import torch

# Example of getting the output of the model for a given text
def tokenize_text(text):
    return tokenizer(text, padding=True, truncation=True, return_tensors="pt")

# Use the model in inference mode and classify a give example
def classify(text):
    inputs = tokenize_text(text)
    print(inputs)
    outputs = model(**inputs)
    return outputs

text = "Hello World"
outputs = classify(text)

print(outputs)

{'input_ids': tensor([[ 101, 7592, 2088,  102]]), 'token_type_ids': tensor([[0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1]])}
BaseModelOutputWithPoolingAndCrossAttentions(last_hidden_state=tensor([[[-0.1689,  0.1361, -0.1394,  ..., -0.6251,  0.0522,  0.3671],
         [-0.3633,  0.1412,  0.8800,  ...,  0.1043,  0.2888,  0.3727],
         [-0.6986, -0.6988,  0.0645,  ..., -0.2210,  0.0099, -0.5940],
         [ 0.8310,  0.1237, -0.1512,  ...,  0.1031, -0.6779, -0.2629]]],
       grad_fn=<NativeLayerNormBackward0>), pooler_output=tensor([[-9.0615e-01, -3.1115e-01, -6.2165e-01,  7.7409e-01,  2.8987e-01,
         -1.9024e-01,  9.2471e-01,  1.8180e-01, -5.0504e-01, -9.9994e-01,
         -2.3735e-01,  8.7621e-01,  9.7716e-01,  2.5809e-01,  9.3802e-01,
         -6.9061e-01, -5.2105e-01, -5.4915e-01,  3.5759e-01, -7.5982e-01,
          6.0571e-01,  9.9936e-01,  3.3454e-01,  2.5202e-01,  4.1586e-01,
          9.7050e-01, -7.8426e-01,  9.3400e-01,  9.6314e-01,  6.5928e-01,
         -7.154

In [42]:
# Download the data locally
# https://huggingface.co/datasets/ucberkeley-dlab/measuring-hate-speech/tree/main

## Read the measuring-hate-speech.parquet
parquet_data = pd.read_parquet('measuring-hate-speech.parquet')

## remove from df the redundant  columns
multilabel_dataset = parquet_data.iloc[:, :-116]


## Remove comment_idm,annotator_id,platform and put the column text in the first position
multilabel_dataset = multilabel_dataset[['text', 'hatespeech', 'sentiment', 'hate_speech_score', 'respect','insult','humiliate','status','dehumanize','violence','genocide' ,'attack_defend']]
multilabel_dataset = multilabel_dataset.iloc[:, 0:2]
# Apply the transformation
multilabel_dataset['hatespeech'] = multilabel_dataset['hatespeech'].apply(lambda x: 1 if x > 0 else 0)
multilabel_dataset.rename(columns={'hatespeech': 'labels'}, inplace=True)
multilabel_dataset


text  labels
0       Yes indeed. She sort of reminds me of the elde...       0
1       The trans women reading this tweet right now i...       0
2       Question: These 4 broads who criticize America...       1
3       It is about time for all illegals to go back t...       0
4       For starters bend over the one in pink and kic...       1
...                                                   ...     ...
135551  عاجل سماحة #السيد_عبدالملك_بدرالدين_الحوثي  نص...       0
135552  Millions of #Yemen-is participated in mass ral...       0
135553  @AbeShinzo @realDonaldTrump @shinzoabe 独裁者は行きま...       0
135554  Millions of #Yemen-is participated in mass ral...       0
135555  لا تتشمت الرجال مسكين يعاني كس امه 😂. يقول يال...       1

[135556 rows x 2 columns]

In [43]:
#Read the new dataset
new_df = pd.read_excel('yeni_data.xlsx')
new_df = new_df[['message', 'Class']]
new_df.rename(columns={'message': 'text', 'Class': 'labels'}, inplace=True)
new_df['labels'] = new_df['labels'].apply(lambda x: 1 if x == 'Hateful' else 0)
new_df



text  labels
0     this is disgusting and heartbreaking. they sho...       1
1     Fuck that cop. Nothing but a fucking thug. \n\...       1
2     Fucking piece of shit cops, protect and serve ...       1
3     Land of the free... My fucking ass. America is...       1
4                These fucking cops are out of control!       1
...                                                 ...     ...
3217  Same with every President. It's in the spotlig...       0
3218  This is sad, I only wish that the illegal immi...       0
3219  I don't feel bad for the guy that was here for...       0
3220  Who feels bad about a person who got caught wi...       0
3221  When people say do the "right way". There is n...       0

[3222 rows x 2 columns]

In [44]:
concatenated_df = pd.concat([new_df, multilabel_dataset], ignore_index=True)
concatenated_df = concatenated_df[concatenated_df['text'] != '']
concatenated_df = concatenated_df[concatenated_df['text'].apply(lambda x: isinstance(x, str))]
concatenated_df['labels']=concatenated_df['labels'].values.tolist()
# Function to convert label to list
def convert_label(label):
    if label == 1:
        return [0, 1] ##means hate speech
    elif label == 0:
        return [1, 0]  ##means no hate speech
    else:
        raise ValueError("Label must be either 0 or 1")

# Apply the function to the label column and create a new column
concatenated_df['labels'] = concatenated_df['labels'].apply(convert_label)
concatenated_df

text  labels
0       this is disgusting and heartbreaking. they sho...  [0, 1]
1       Fuck that cop. Nothing but a fucking thug. \n\...  [0, 1]
2       Fucking piece of shit cops, protect and serve ...  [0, 1]
3       Land of the free... My fucking ass. America is...  [0, 1]
4                  These fucking cops are out of control!  [0, 1]
...                                                   ...     ...
138773  عاجل سماحة #السيد_عبدالملك_بدرالدين_الحوثي  نص...  [1, 0]
138774  Millions of #Yemen-is participated in mass ral...  [1, 0]
138775  @AbeShinzo @realDonaldTrump @shinzoabe 独裁者は行きま...  [1, 0]
138776  Millions of #Yemen-is participated in mass ral...  [1, 0]
138777  لا تتشمت الرجال مسكين يعاني كس امه 😂. يقول يال...  [0, 1]

[138777 rows x 2 columns]

In [45]:
## Preprocess the TEXT data
## Remove HTML tags
def remove_html_tags(text):
    clean = re.compile('<.*?>')
    return re.sub(clean, '', text)

concatenated_df['text'] = concatenated_df['text'].apply(lambda x: remove_html_tags(x))

## Remove URL
def remove_url(text):
    return re.sub(r'http\S+', '', text)

concatenated_df['text'] = concatenated_df['text'].apply(lambda x: remove_url(x))

## Lowercase
concatenated_df['text'] = concatenated_df['text'].str.lower()

## Remove punctuation
def remove_punctuation(text):
    return re.sub(r'[^\w\s]', '', text)

concatenated_df['text'] = concatenated_df['text'].apply(lambda x: remove_punctuation(x))

## Handling Contractions using libraries

def expand_contractions(text):
    return contractions.fix(text)

concatenated_df['text'] = concatenated_df['text'].apply(lambda x: expand_contractions(x))

## Remove stopwords
nltk.download('stopwords')
stop_words = set(stopwords.words('english'))

def remove_stopwords(text):
    return " ".join([word for word in str(text).split() if word not in stop_words])

concatenated_df['text'] = concatenated_df['text'].apply(lambda x: remove_stopwords(x))

## Lemmatization
nltk.download('wordnet')
lemmatizer = WordNetLemmatizer()

def lemmatize_words(text):
    return " ".join([lemmatizer.lemmatize(word) for word in text.split()])
concatenated_df['text'] = concatenated_df['text'].apply(lambda x: lemmatize_words(x))

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


In [46]:
MAX_LEN = 256
TRAIN_BATCH_SIZE = 16
VALID_BATCH_SIZE = 8
EPOCHS = 10
LEARNING_RATE = 1e-05

In [47]:
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')

In [48]:
import torch
from torch.utils.data import Dataset

class HateSpeechDataset(Dataset):
    def __init__(self, data, tokenizer,max_len=256):

        self.tokenizer = tokenizer
        self.data = data
        self.text = data.text
        self.targets = self.data.labels
        self.max_len = max_len

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):

        text = str(self.text.iloc[idx])

        encoding = self.tokenizer.encode_plus(
            text,
            add_special_tokens=True,
            max_length=self.max_len,
            padding='max_length',
            truncation=True,
            return_token_type_ids=True
        )


        ids = encoding['input_ids']
        mask = encoding['attention_mask']
        token_type_ids = encoding['token_type_ids']

        return {
            'input_ids': torch.tensor(ids, dtype=torch.long),
            'attention_mask': torch.tensor(mask, dtype=torch.long),
            'token_type_ids': torch.tensor(token_type_ids, dtype=torch.long),
            'targets': torch.tensor(self.targets.iloc[idx], dtype=torch.float).to(device)
        }

In [49]:
train_texts, val_texts,= train_test_split(concatenated_df,test_size=0.2)

print("Dataset length: {}".format(concatenated_df.shape))
print("Train Dataset length: {}".format(train_texts.shape))
print("Val Dataset length: {}".format(val_texts.shape))

Dataset length: (138777, 2)
Train Dataset length: (111021, 2)
Val Dataset length: (27756, 2)


In [50]:
training_dataset = HateSpeechDataset(train_texts,tokenizer,MAX_LEN)
validation_dataset = HateSpeechDataset(val_texts,tokenizer,MAX_LEN)

In [51]:
train_params = {'batch_size': TRAIN_BATCH_SIZE,
                'shuffle': True,
                'num_workers': 0
                }

test_params = {'batch_size': VALID_BATCH_SIZE,
                'shuffle': True,
                'num_workers': 0
                }

training_loader = DataLoader(training_dataset, **train_params)
validation_loader = DataLoader(validation_dataset, **test_params)

In [52]:
next(iter(training_loader))

{'input_ids': tensor([[  101,  2157,  3272,  ...,     0,     0,     0],
         [  101,  2748,  3347,  ...,     0,     0,     0],
         [  101, 11560,  2215,  ...,     0,     0,     0],
         ...,
         [  101, 19465,  2242,  ...,     0,     0,     0],
         [  101,  2893,  5837,  ...,     0,     0,     0],
         [  101, 10021, 10722,  ...,     0,     0,     0]]),
 'attention_mask': tensor([[1, 1, 1,  ..., 0, 0, 0],
         [1, 1, 1,  ..., 0, 0, 0],
         [1, 1, 1,  ..., 0, 0, 0],
         ...,
         [1, 1, 1,  ..., 0, 0, 0],
         [1, 1, 1,  ..., 0, 0, 0],
         [1, 1, 1,  ..., 0, 0, 0]]),
 'token_type_ids': tensor([[0, 0, 0,  ..., 0, 0, 0],
         [0, 0, 0,  ..., 0, 0, 0],
         [0, 0, 0,  ..., 0, 0, 0],
         ...,
         [0, 0, 0,  ..., 0, 0, 0],
         [0, 0, 0,  ..., 0, 0, 0],
         [0, 0, 0,  ..., 0, 0, 0]]),
 'targets': tensor([[1., 0.],
         [1., 0.],
         [0., 1.],
         [0., 1.],
         [1., 0.],
         [0., 1.],
    

In [53]:

print(model)

BertModel(
  (embeddings): BertEmbeddings(
    (word_embeddings): Embedding(30522, 768, padding_idx=0)
    (position_embeddings): Embedding(512, 768)
    (token_type_embeddings): Embedding(2, 768)
    (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (encoder): BertEncoder(
    (layer): ModuleList(
      (0-11): 12 x BertLayer(
        (attention): BertAttention(
          (self): BertSdpaSelfAttention(
            (query): Linear(in_features=768, out_features=768, bias=True)
            (key): Linear(in_features=768, out_features=768, bias=True)
            (value): Linear(in_features=768, out_features=768, bias=True)
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (output): BertSelfOutput(
            (dense): Linear(in_features=768, out_features=768, bias=True)
            (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
            (dropout): Dropout(p=0.1, inplace=False

In [54]:
# Creating the customized model, by adding a drop out and a dense layer on top of distil bert to get the final output for the model.

class MultilabelHateBert(torch.nn.Module):
    def __init__(self,bertmodel):
        super(MultilabelHateBert, self).__init__()
        self.bertmodel = bertmodel
        self.dropout = torch.nn.Dropout(0.3)
        self.linear = torch.nn.Linear(768, 2)

    def forward(self, ids, mask, token_type_ids):

      output_1= self.bertmodel(ids, attention_mask = mask, token_type_ids = token_type_ids)
      output_2 = self.dropout(output_1.pooler_output)
      output = self.linear(output_2)
      return output

multilabel_model = MultilabelHateBert(model)
multilabel_model.to(device)

MultilabelHateBert(
  (bertmodel): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSdpaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, e

In [55]:
def criterion(outputs, targets):
    return torch.nn.BCEWithLogitsLoss()(outputs, targets)

In [56]:

optimizer = torch.optim.Adam(params =  multilabel_model.parameters(), lr=LEARNING_RATE)

In [60]:
results_models_weights_dir = 'models_weights_with_bert_vast_ai/'
if not os.path.exists(results_models_weights_dir):
    os.mkdir(results_models_weights_dir)

In [61]:
### Osman Changed this part
from tqdm import tqdm
from sklearn import metrics

total_loss = 0.0
batch_count = 0

for epoch in tqdm(range(EPOCHS), desc="Epochs"):

  multilabel_model.train()

  for i, batch in tqdm(enumerate(training_loader), desc=f"Epoch {epoch + 1}", total=len(training_loader)):

    input_ids = batch['input_ids'].to(device)
    attention_mask = batch['attention_mask'].to(device)
    token_type_ids = batch['token_type_ids'].to(device)
    targets = batch['targets'].to(device)
    #I moved optimizer.zero_grad() to here, and deleted one of them
    optimizer.zero_grad()
    outputs = multilabel_model(input_ids,attention_mask,token_type_ids)
    #optimizer.zero_grad()
    #print("Outputs:",outputs)
    #print("Targets:",targets)
    loss = criterion(outputs,targets)

    total_loss += loss.item()
    batch_count += 1
    if i%50==0:
      print()
      print(f'Epoch: {epoch}, Loss{total_loss/batch_count}')

    #optimizer.zero_grad()
    loss.backward()
    optimizer.step()
  torch.save(multilabel_model.state_dict(), results_models_weights_dir + 'base_model_bert.pth')
  print("Model state saved for Epoch:", epoch)


  ####Evaluationnn
  multilabel_model.eval()
  val_targets=[]
  val_outputs=[]

  with torch.no_grad():

    for i,batch in enumerate(validation_loader):

      input_ids = batch['input_ids'].to(device)
      attention_mask = batch['attention_mask'].to(device)
      token_type_ids = batch['token_type_ids'].to(device)
      targets = batch['targets'].to(device)

      outputs = multilabel_model(input_ids,attention_mask,token_type_ids)

      val_targets.extend(targets.cpu().detach().numpy().tolist())
      val_outputs.extend(torch.sigmoid(outputs).cpu().detach().numpy().tolist())

  outputs = np.array(val_outputs) >= 0.5
  accuracy = metrics.accuracy_score(val_targets, outputs)
  f1_score_micro = metrics.f1_score(val_targets, outputs, average='micro')
  f1_score_macro = metrics.f1_score(val_targets, outputs, average='macro')
  print(f"Accuracy Score = {accuracy}")
  print(f"F1 Score (Micro) = {f1_score_micro}")
  print(f"F1 Score (Macro) = {f1_score_macro}")




Epoch 1:   0%|          | 1/6939 [00:00<17:29,  6.61it/s]


Epoch: 0, Loss0.6084232330322266



Epoch 1:   1%|          | 51/6939 [00:14<32:59,  3.48it/s]


Epoch: 0, Loss0.5647377476972693



Epoch 1:   1%|▏         | 101/6939 [00:28<33:24,  3.41it/s]

...


Epoch: 9, Loss0.32741821792366077



Epoch 10: 100%|██████████| 6939/6939 [35:26<00:00,  3.26it/s]


Model state saved for Epoch: 9


Epochs: 100%|██████████| 10/10 [6:25:59<00:00, 2315.92s/it]

Accuracy Score = 0.7892707882980257
F1 Score (Micro) = 0.7896140401455908
F1 Score (Macro) = 0.7821986251955074
